In [2]:
import torch
import torch.nn as nn
import torch.optim as optim

In [13]:
# ターゲットモデル: 64次元の行動記述子を入力とする全結合ネットワーク
class TargetModel(nn.Module):
    def __init__(self):
        super(TargetModel, self).__init__()
        self.fc1 = nn.Linear(64, 128)  # 64次元BDを128次元に変換
        self.fc2 = nn.Linear(128, 256) # 128次元を256次元に変換
        self.fc3 = nn.Linear(256, 512) # 最終的に512次元に変換
    
    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = self.fc3(x)
        return x

# 予測モデル: 64次元の行動記述子を入力とする全結合ネットワーク
class PredictorModel(nn.Module):
    def __init__(self):
        super(PredictorModel, self).__init__()
        self.fc1 = nn.Linear(64, 512)  # 512次元の入力を512次元に保持
        self.fc2 = nn.Linear(512, 512)  # 512次元の出力を生成
    
    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = self.fc2(x)
        return x

# SND-Vの損失関数: ターゲットと予測のL2距離を計算
def snd_v_loss(target, predictor):
    distance = torch.norm(target - predictor, p=2, dim=1)  # L2ノルム（ユークリッド距離）
    return torch.mean(distance)

# トレーニングループの例
def train_snd_v(target_model, predictor_model, optimizer, data_loader):
    target_model.train()
    predictor_model.train()

    for batch in data_loader:
        bd = batch['bd']  # 64次元の行動記述子 (Behavior Descriptor)
        target_output = target_model(bd)
        predictor_output = predictor_model(bd)

        # 損失を計算
        loss = snd_v_loss(target_output, predictor_output)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        print(f"損失: {loss.item()}")

In [17]:
# モデル、オプティマイザーの初期化
target_model = TargetModel()
predictor_model = PredictorModel()
optimizer = optim.Adam(list(target_model.parameters()) + list(predictor_model.parameters()), lr=1e-4)

# 仮のデータローダの例
class DummyDataLoader:
    def __init__(self):
        self.data = torch.randn(64, 64)  # 64次元の行動記述子を64個生成

    def __iter__(self):
        return self

    def __next__(self):
        return {'bd': self.data}  # バッチデータを返す
    
data_loader = DummyDataLoader()

counter = 0
for data in data_loader:
    print(data['bd'].shape)  # 64次元の行動記述子が64個のバッチデータとして返される
    counter += 1
    
    if counter >= 10:
        break

torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])
torch.Size([64, 64])


In [15]:
# データローダの仮定：64次元の行動記述子をバッチで提供
train_snd_v(target_model, predictor_model, optimizer, data_loader)

損失: 5.890415191650391
損失: 5.699699401855469
損失: 5.520884990692139
損失: 5.354073524475098
損失: 5.199162483215332
損失: 5.055850505828857
損失: 4.923608779907227
損失: 4.801782131195068
損失: 4.689582824707031
損失: 4.586179256439209
損失: 4.490699768066406
損失: 4.402263164520264
損失: 4.320008754730225
損失: 4.243138313293457
損失: 4.170901298522949
損失: 4.102644443511963
損失: 4.037788391113281
損失: 3.9758245944976807
損失: 3.916313886642456
損失: 3.858883857727051
損失: 3.8032217025756836
損失: 3.7490737438201904
損失: 3.696218490600586
損失: 3.6444828510284424
損失: 3.593710422515869
損失: 3.543779134750366
損失: 3.494591236114502
損失: 3.446065664291382
損失: 3.3981165885925293
損失: 3.350695848464966
損失: 3.3037590980529785
損失: 3.2572731971740723
損失: 3.211216926574707
損失: 3.165571928024292
損失: 3.1203339099884033
損失: 3.075495481491089
損失: 3.0310540199279785
損失: 2.9870195388793945
損失: 2.943394184112549
損失: 2.9001736640930176
損失: 2.8573505878448486
損失: 2.8149337768554688
損失: 2.772925853729248
損失: 2.731332302093506
損失: 2.6901402473449

KeyboardInterrupt: 